In [1]:
import numpy as np
import pandas as pd

# Add lab library
import sys
sys.path.insert(0, '/home/trevormjs/Documents/Science/APL/Lab')


#---------------------------------------------------------------------#
#                        matplotlib plotting                          #
#---------------------------------------------------------------------#
import matplotlib.pyplot as plt
import matplotlib as mpl
from jupyterthemes import jtplot
from Helper.plotting import my_graph
# Edit the font, font size, and axes width
# mpl.rcParams['font.family'] = 'Avenir'
plt.rcParams['font.size'] = 24
plt.rcParams['axes.linewidth'] = 2
jtplot.style(theme='monokai', context='notebook', ticks=False, grid=False)

#---------------------------------------------------------------------#
#                           bokeh plotting                            #
#---------------------------------------------------------------------#
from bokeh.plotting import figure, show, output_notebook
from bokeh.themes import Theme
from bokeh.io import curdoc, export_png
from bokeh.models import Range1d, Label, ColumnDataSource, LabelSet
from Helper.plotting import style
output_notebook()
# curdoc().theme = Theme(filename="../Helper/theme.yml")

#---------------------------------------------------------------------#
#                       error and unit handling                       #
#---------------------------------------------------------------------#
from uncertainties import ufloat
import Helper.numbers as nu
from Helper.record import Measurement, Unit

%load_ext autoreload
%autoreload 2



Loading BokehJS ...

In [56]:
def read_scope_csv(path, n_sigs = 1):
    ret = []
    for n in range(n_sigs):
        config = pd.read_csv(path, header=None, usecols=[1+6*n, 2+6*n]).loc[:2]
        config = [record_length, sample_interval, trigger_point] = [
            [float(val), unit] for val, unit in zip(config[1+6*n], config[2+6*n])]
        config= {
            'record_length': record_length,
            'sample_interval': sample_interval,
            'trigger_point': trigger_point
        }
        display(config)
        data = pd.read_csv(path, header = None, usecols=[3+6*n, 4+6*n])
        data.columns = ['ts', 'mV']
        ret.append([data, config])
    return ret

### Test Pulse, Scope, and Laser Diode

In [59]:
[[squares, squares_config]] = read_scope_csv('./Data/l4_A_1_data.csv')

{'record_length': [10000.0, 'Points'],
 'sample_interval': [3.99999989e-09, 's'],
 'trigger_point': [4640.00039, 'Samples']}

In [31]:
fig = figure()
fig.line(squares.ts, squares.mV)
show(fig)

In [52]:
approx_amplitude = squares.mV.max() - squares.mV.min()
fourier_coefs = np.fft.fft(squares.mV, n=len(squares)*8)
fourier_freqs = np.fft.fftfreq(
    len(squares.mV)*8, squares_config['sample_interval'][0]
)

pulse_frequency = fourier_freqs[
    10:len(fourier_freqs)//2][
    fourier_coefs[10:len(fourier_freqs)//2].argmax()
]

approx_amplitude, 'mV', pulse_frequency, 'Hz'

(5.5999997545, 'mV', 90625.00249218756, 'Hz')

In [50]:
fig = figure()
fig.line(fourier_freqs, np.abs(fourier_coefs))
show(fig)

### Initial Optics Setup

In [87]:
[[pd1, pd1_config], [pd2, pd2_config]] = read_scope_csv(
    './Data/l4_C_data.csv', 2)

fig = figure()
fig.line(pd1.ts, pd1.mV, legend_label='PD1')
fig.line(pd1.ts, pd2.mV, legend_label='PD2', color='red')
show(fig)

{'record_length': [10000.0, 'Points'],
 'sample_interval': [1.9999999e-09, 's'],
 'trigger_point': [5020.00004, 'Samples']}

{'record_length': [10000.0, 'Points'],
 'sample_interval': [1.9999999e-09, 's'],
 'trigger_point': [5020.00004, 'Samples']}

In [88]:
[[pd1, pd1_config], [pd2, pd2_config]] = read_scope_csv(
    './Data/l4_C_data3.csv', 2)

fig = figure()
fig.line(pd1.ts, pd1.mV, legend_label='PD1')
fig.line(pd1.ts, nu.fft_filter(pd2.mV, .17), legend_label='PD2', color='red')
show(fig)

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4834.00032, 'Samples']}

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4834.00032, 'Samples']}

In [135]:
[[pd1, pd1_config], [pd2, pd2_config]] = read_scope_csv(
    './Data/l4_C_data4.csv', 2)

fig = figure()
fig.line(pd1.ts, pd1.mV, legend_label='PD1')
fig.line(pd1.ts, pd2.mV, legend_label='PD2', color='red')
show(fig)

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4932.80043, 'Samples']}

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4932.80043, 'Samples']}

In [197]:
fig = figure()
pd1_clean = pd.Series(nu.fft_filter(pd1.mV, .24))
pd2_clean = pd.Series(nu.fft_filter(pd2.mV, .24))
fig.line(pd1.ts, pd1_clean, legend_label='PD1')
fig.line(pd1.ts, pd2_clean, legend_label='PD2', color='red')

pd1_inds, pd1_90_10_inds = rising_edge(pd1_clean, pd1.ts)
fig.scatter(pd1.ts[pd1_inds], pd1_clean[pd1_inds])
fig.scatter(pd1.ts[pd1_90_10_inds], pd1_clean[pd1_90_10_inds], color='skyblue')

pd2_inds, pd2_90_10_inds = rising_edge(pd2_clean, pd1.ts)
fig.scatter(pd1.ts[pd2_inds], pd2_clean[pd2_inds], color='red')
fig.scatter(pd1.ts[pd2_90_10_inds], pd2_clean[pd2_90_10_inds], color='pink')

fig.x_range = Range1d(-4e-9, 5e-8)
show(fig)

0.060274768393727016 0.058051481195171624
2.0000000712810003e-09
0.04748231563388587 0.04637055516794694
2.2000001799999994e-09


In [138]:
from scipy.signal import peak_widths

In [143]:
from bokeh.palettes import Category20_4 as colors

In [199]:
fig = figure()
pd1_cable_clean = pd.Series(nu.fft_filter(pd1_cable.mV, .24))
pd2_cable_clean = pd.Series(nu.fft_filter(pd2_cable.mV, .24))
fig.line(pd1_cable.ts, pd1_cable_clean, legend_label='pd1_cable')
fig.line(pd1_cable.ts, pd2_cable_clean, legend_label='pd2_cable', color='red')

pd1_cable_inds, pd1_cable_90_10_inds = rising_edge(
    pd1_cable_clean, pd1_cable.ts)
fig.scatter(pd1_cable.ts[pd1_cable_inds], pd1_cable_clean[pd1_cable_inds])
fig.scatter(pd1_cable.ts[pd1_cable_90_10_inds],
            pd1_cable_clean[pd1_cable_90_10_inds], color='skyblue')

pd2_cable_inds, pd2_cable_90_10_inds = rising_edge(
    pd2_cable_clean, pd1_cable.ts)
fig.scatter(pd1_cable.ts[pd2_cable_inds],
            pd2_cable_clean[pd2_cable_inds], color='red')
fig.scatter(pd1_cable.ts[pd2_cable_90_10_inds],
            pd2_cable_clean[pd2_cable_90_10_inds], color='pink')

fig.x_range = Range1d(-4e-9, 5e-8)
show(fig)

0.06274893912436255 0.06133876594531695
2.000000079649e-09
0.011080261607846777 0.01086577116549486
2.400000155e-09


In [245]:
def rising_edge(sig, times):

    max_ind, max_val = sig.idxmax(), sig.max()
    this_ind, this_val = max_ind, max_val
    next_ind = max_ind - 2
    next_val = sig[next_ind]

    while this_val - next_val > 0:
        this_ind = next_ind
        this_val = next_val
        next_ind -= 1
        if next_ind == -1:
            break
        next_val = sig[next_ind]

    start_ind = this_ind
    end_ind = max_ind

    rising_slice = sig[start_ind:end_ind]
    ran = rising_slice.tolist()[-1] - rising_slice.tolist()[0]
    ten = rising_slice.tolist()[0] + .1*ran
    ninety = rising_slice.tolist()[-1] - .1*ran
    ten_ind = rising_slice[rising_slice < ten].index[-1]
    ninety_ind = rising_slice[rising_slice < ninety].index[-1]
    rising_time = times[ninety_ind] - times[ten_ind]

    return [[start_ind, end_ind], [ten_ind, ninety_ind]]

In [247]:
fig = figure()

"""
Create a time vector beginning at zero for alignment purposes.
"""
t = pd1.loc[pd1.ts >= 0, 'ts']
t.index = range(len(t))

"""
Filter all curves such that they are identical. This is really for
ease of processing but also because they really should be identical,
and any differences must represent some error.
"""
pd1_cable_clean = pd.Series(nu.fft_filter(pd1_cable.mV, .14))
pd1_clean = pd.Series(nu.fft_filter(pd1.mV, .123))

pd2_cable_clean = pd.Series(nu.fft_filter(pd2_cable.mV, .14))
pd2_clean = pd.Series(nu.fft_filter(pd2.mV, .1))

"""
Caclulate the indeces of the rising edge for all signals, and the
locations of 10% and 90%.
"""
pd1_cable_inds, pd1_cable_90_10_inds = rising_edge(
    pd1_cable_clean, pd1_cable.ts)
pd1_inds, pd1_90_10_inds = rising_edge(
    pd1_clean, pd1_cable.ts)

pd2_cable_inds, pd2_cable_90_20_inds = rising_edge(
    pd2_cable_clean, pd2_cable.ts)
pd2_inds, pd2_90_20_inds = rising_edge(
    pd2_clean, pd2_cable.ts)

"""
Align each PD1 curve to the beginning of its rising edge.
Align each PD2 curve to the beginning of the rising edge of
the corresponding PD1.
"""
zi_pd1_cable = pd1_cable_clean[pd1_cable_inds[0]:]
zi_pd1 = pd1_clean[pd1_inds[0]:]

zi_pd2_cable = pd2_cable_clean[pd1_cable_inds[0]:]
zi_pd2 = pd2_clean[pd1_inds[0]:]

"""
Normalize each signal on the scale [0, 1].
"""
zi_pd1_cable -= zi_pd1_cable.min()
zi_pd2_cable -= zi_pd2_cable.min()
zi_pd1_cable /= zi_pd1_cable.max()
zi_pd2_cable /= zi_pd2_cable.max()

zi_pd1 -= zi_pd1.min()
zi_pd2 -= zi_pd2.min()
zi_pd1 /= zi_pd1.max()
zi_pd2 /= zi_pd2.max()

"""
Plot each pair of PD1 and PD2 signals, and calculate
their locations of etc.
"""
results = {}
for sig, name, color in zip(
    [zi_pd1_cable, zi_pd1, zi_pd2_cable, zi_pd2],
    ['PD1_cable', 'PD1', 'PD2_cable', 'PD2'],
    colors
):
    sig.index = range(len(sig))
    fig.line(t,
             sig[:len(t)],
             legend_label=name,
             color=color,
             line_width=1.6)
    times = rising_edge(sig[:len(t)], t)
    times = times[0] + times[1]
    results.update({name:[t[i] for i in times]})
    
fig.x_range = Range1d(-.4e-9, 3e-8)
show(fig)
results = pd.DataFrame(results, index = ['start','stop','10','90']).T

In [258]:
diffs = pd.DataFrame(results.T[['PD2_cable', 'PD2']].values -
                     results.T[['PD1_cable', 'PD1']].values,
                     index=results.columns,
                     columns=['cable_diff', 'no-cable_diff'])
(diffs.cable_diff-diffs['no-cable_diff']).mean(), (diffs.cable_diff-diffs['no-cable_diff']).std()

(4.9000001643177495e-09, 2.000001800312607e-10)